# **Bitcoin price forecasting - Linear Regression**
### Big Data Computing final project - A.Y. 2022 - 2023
Prof. Gabriele Tolomei

MSc in Computer Science

La Sapienza, University of Rome

### Author
Corsi Danilo - corsi.1742375@studenti.uniroma1.it



## Global constants, dependencies, libraries and tools

In [1]:
# GDrive root
GDRIVE_DIR = "/content/drive"

# Dataset
GDRIVE_DATASET_OUTPUT_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/datasets/output"
GDRIVE_DATASET_NAME = "bitcoin_blockchain_data_30min"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_NAME + "_train_valid"
GDRIVE_DATASET_NAME_EXT_ENG  = "/" + GDRIVE_DATASET_NAME_ENG + ".parquet"
GDRIVE_DATASET_NAME_ENG = GDRIVE_DATASET_OUTPUT_DIR + GDRIVE_DATASET_NAME_EXT_ENG

# Features
GDRIVE_FEATURES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/features"
GDRIVE_ALL_FEATURES_NAME = "all_features"
GDRIVE_MORE_REL_FEATURES_NAME = "more_rel_features"
GDRIVE_LESS_REL_FEATURES_NAME = "less_rel_features"
GDRIVE_ALL_FEATURES_NAME_EXT = "/" + GDRIVE_ALL_FEATURES_NAME + ".json"
GDRIVE_MORE_REL_FEATURES_NAME_EXT = "/" + GDRIVE_MORE_REL_FEATURES_NAME + ".json"
GDRIVE_LESS_REL_FEATURES_NAME_EXT = "/" + GDRIVE_LESS_REL_FEATURES_NAME + ".json"
GDRIVE_ALL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_ALL_FEATURES_NAME_EXT
GDRIVE_MORE_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_MORE_REL_FEATURES_NAME_EXT
GDRIVE_LESS_REL_FEATURES = GDRIVE_FEATURES_DIR + GDRIVE_LESS_REL_FEATURES_NAME_EXT

# Others
JAVA_HOME = "/usr/lib/jvm/java-8-openjdk-amd64"
MODEL_NAME = "LinearRegression"
SLOW_OPERATION = True

In [2]:
# Point Colaboratory to our Google Drive
from google.colab import drive

# Define GDrive paths
drive.mount(GDRIVE_DIR, force_remount=True)

Mounted at /content/drive


In [3]:
import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

In [4]:
# Install Spark and related dependencies
!pip install pyspark

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 310.8/310.8 MB 4.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for pyspark: filename=pyspark-3.4.1-py2.py3-none-any.whl size=311285388 sha256=2c297c337ec10f01dd9263f53238d1ae9b8cb331f53c55597125a0ef8f2527d8
  Stored in directory: /root/.cache/pip/wheels/0d/77/a3/ff2f74cc9ab41f8f594dabf0579c2a7c6de920d584206e0834
Successfully built pyspark


## Import files

In [28]:
GDRIVE_UTILITIES_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/utilities"

import sys
sys.path.append(GDRIVE_UTILITIES_DIR)

from imports import *
import utilities, parameters

importlib.reload(utilities)
importlib.reload(parameters)

<module 'parameters' from '/content/drive/MyDrive/BDC/project/utilities/parameters.py'>

## Create the pyspark session

In [6]:
# Create the session
conf = SparkConf().\
                set('spark.ui.port', "4050").\
                set('spark.executor.memory', '4G').\
                set('spark.driver.memory', '45G').\
                set('spark.driver.maxResultSize', '10G').\
                set("spark.kryoserializer.buffer.max", "1G").\
                setAppName("BitcoinPriceForecasting").\
                setMaster("local[*]")

# Create the context
sc = pyspark.SparkContext(conf=conf)
spark = SparkSession.builder.getOrCreate()

## Loading dataset

In [7]:
# Load datasets into pyspark dataframe objects
df = spark.read.load(GDRIVE_DATASET_NAME_ENG,
                         format="parquet",
                         sep=",",
                         inferSchema="true",
                         header="true"
                    )

In [8]:
def dataset_info(dataset):
  dataset.show(3)

  # Get the number of rows
  num_rows = dataset.count()

  # Get the number of columns
  num_columns = len(dataset.columns)

  # Print the shape of the DataFrame
  print("Shape:", (num_rows, num_columns))

  # Print the schema of the DataFrame
  dataset.printSchema()

In [9]:
if SLOW_OPERATION:
  dataset_info(df)

+-------------------+---+------------------+--------------+-------------------+--------------+------------------+------------------+--------------------+------------------------+-----------------+-------------------+------------------+--------------------+------------------+------------------+--------------------------------+--------------------+------------------+------------------+------------------+------------------+------------------+------------------+
|          timestamp| id|      market-price|total-bitcoins|         market-cap|  trade-volume|       blocks-size|    avg-block-size|n-transactions-total|n-transactions-per-block|        hash-rate|         difficulty|    miners-revenue|transaction-fees-usd|n-unique-addresses|    n-transactions|estimated-transaction-volume-usd|      rate-of-change|        sma-5-days|        sma-7-days|       sma-10-days|       sma-20-days|       sma-50-days|      sma-100-days|
+-------------------+---+------------------+--------------+---------------

## Loading features

In [10]:
# Set the features label
FEATURES_LABEL = "features"

# Set the target variable
TARGET_VAL = 'market-price'

In [11]:
# Loading correlation matrix features
with open(GDRIVE_ALL_FEATURES, "r") as f:
    all_features = json.load(f)
print(all_features)

['total-bitcoins', 'market-cap', 'trade-volume', 'blocks-size', 'avg-block-size', 'n-transactions-total', 'n-transactions-per-block', 'hash-rate', 'difficulty', 'miners-revenue', 'transaction-fees-usd', 'n-unique-addresses', 'n-transactions', 'estimated-transaction-volume-usd', 'rate-of-change', 'sma-5-days', 'sma-7-days', 'sma-10-days', 'sma-20-days', 'sma-50-days', 'sma-100-days']


In [12]:
# Loading correlation matrix features
with open(GDRIVE_MORE_REL_FEATURES, "r") as f:
    more_rel_features = json.load(f)
print(more_rel_features)

['market-cap', 'miners-revenue', 'sma-5-days', 'sma-7-days', 'estimated-transaction-volume-usd', 'sma-10-days', 'n-transactions-total', 'blocks-size', 'sma-100-days', 'total-bitcoins']


In [13]:
# Loading correlation matrix features
with open(GDRIVE_LESS_REL_FEATURES, "r") as f:
    less_rel_features = json.load(f)
print(less_rel_features)

['sma-20-days', 'sma-50-days', 'n-unique-addresses', 'difficulty', 'hash-rate', 'avg-block-size', 'transaction-fees-usd', 'trade-volume', 'n-transactions-per-block', 'n-transactions', 'rate-of-change']


## Evaluate simple model

In [14]:
# Get default params
params = parameters.get_defaults_model_params(MODEL_NAME)
params

{'maxIter': [100], 'regParam': [0.0], 'elasticNetParam': [0.0]}

In [15]:
# Valid performances with all the features
simple_res_all, simple_pred_all = utilities.evaluate_simple_model(df, all_features, params, GDRIVE_ALL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
simple_res_all

Model    Type      Features       Parameters         RMSE  \
0  LinearRegression  simple  all_features  [100, 0.0, 0.0]  4288.585097   

       MAPE          MAE      Variance        R2  Adjusted_R2      Time  
0  0.124091  3461.845228  1.501965e+08  0.900484      0.90046  6.229855

In [16]:
utilities.show_results(simple_pred_all, MODEL_NAME, TARGET_VAL)

In [17]:
# Valid performances with the corr matrix features
simple_res_more_rel, simple_pred_more_rel = utilities.evaluate_simple_model(df, more_rel_features, params, GDRIVE_MORE_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
simple_res_more_rel

Model    Type           Features       Parameters         RMSE  \
0  LinearRegression  simple  more_rel_features  [100, 0.0, 0.0]  9026.635554   

       MAPE          MAE      Variance        R2  Adjusted_R2      Time  
0  0.219481  6967.905283  3.650631e+07  0.559123     0.559019  2.424016

In [18]:
utilities.show_results(simple_pred_more_rel, MODEL_NAME, TARGET_VAL)

In [19]:
# Valid performances with the corr matrix features
simple_res_less_rel, simple_pred_less_rel = utilities.evaluate_simple_model(df, less_rel_features, params, GDRIVE_LESS_REL_FEATURES_NAME, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
simple_res_less_rel

Model    Type           Features       Parameters          RMSE  \
0  LinearRegression  simple  less_rel_features  [100, 0.0, 0.0]  14182.539053   

       MAPE           MAE      Variance        R2  Adjusted_R2      Time  
0  0.314191  10899.108275  6.582993e+07 -0.088363     -0.08862  2.362139

In [20]:
utilities.show_results(simple_pred_less_rel, MODEL_NAME, TARGET_VAL)

## Hyperparameter tuning

In [29]:
choosen_features = more_rel_features
CHOSEN_FEATURES_LABEL = GDRIVE_MORE_REL_FEATURES_NAME

In [30]:
# Split proportion list
PORTION_LIST = [0.6, 0.7, 0.8, 0.9]

In [31]:
# Get simple params
params = parameters.get_model_params(MODEL_NAME)
params

{'maxIter': [5, 10, 50, 80, 100],
 'regParam': array([0. , 0.2, 0.4, 0.6, 0.8]),
 'elasticNetParam': array([0. , 0.2, 0.4, 0.6, 0.8])}

In [32]:
hyp_res, hyp_params= utilities.autoTuning(df, choosen_features, params, CHOSEN_FEATURES_LABEL, PORTION_LIST, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
hyp_res

Model        Type           Features  Proportion     Parameters  \
0  LinearRegression  autotuning  more_rel_features         0.9  [5, 0.2, 0.4]   

          RMSE      MAPE          MAE      Variance        R2  Adjusted_R2  \
0  1942.436008  0.068752  1465.138704  7.577615e+06  0.587808     0.587613   

       Time  
0  0.345756

## Cross validation

In [33]:
# Get tuned params
params = hyp_params
params

{'maxIter': [5], 'regParam': [0.2], 'elasticNetParam': [0.4]}

In [34]:
## Cross Validation Parameter
# Multiple Splits Time Series Cross Validation
mul_cv = {'cv_type':'mulTs',
          'kSplits': 5}

# Blocked Time Series Cross Validation
blk_cv = {'cv_type':'blkTs',
          'kSplits': 10}

In [35]:
mul_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, mul_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
mul_cv_res

Model   Type           Features  Splits Train&Validation  \
0  LinearRegression  mulTs  more_rel_features       1   (21182, 21181)   
1  LinearRegression  mulTs  more_rel_features       2   (42363, 21181)   
2  LinearRegression  mulTs  more_rel_features       3   (63544, 21181)   
3  LinearRegression  mulTs  more_rel_features       4   (84725, 21181)   
4  LinearRegression  mulTs  more_rel_features       5  (105906, 21181)   

      Parameters          RMSE      MAPE           MAE      Variance  \
0  [5, 0.2, 0.4]   6356.530663  0.625849   4880.643357  2.385892e+07   
1  [5, 0.2, 0.4]   1415.177725  0.150214    976.261954  1.309760e+06   
2  [5, 0.2, 0.4]   2547.189992  0.232624   2258.207756  5.536040e+06   
3  [5, 0.2, 0.4]  36031.852059  0.744761  33605.271682  1.129568e+09   
4  [5, 0.2, 0.4]  11008.947949  0.296967   8789.106567  9.527260e+07   

         R2  Adjusted_R2      Time  
0 -1.265295    -1.265937  0.489180  
1  0.622031     0.621923  0.631226  
2 -1.556528    -1.557252  0.721277  
3 -6.330322    -6.332399  0.863575  
4 -0.459408    -0.459822  0.996880

In [36]:
blk_cv_res, trained_models_mul_cv = utilities.tsCrossValidation(df, choosen_features, params, blk_cv, CHOSEN_FEATURES_LABEL, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)
blk_cv_res

Model   Type           Features  Splits Train&Validation  \
0  LinearRegression  blkTs  more_rel_features       1    (10166, 2542)   
1  LinearRegression  blkTs  more_rel_features       2    (10166, 2542)   
2  LinearRegression  blkTs  more_rel_features       3    (10166, 2542)   
3  LinearRegression  blkTs  more_rel_features       4    (10166, 2542)   
4  LinearRegression  blkTs  more_rel_features       5    (10166, 2542)   
5  LinearRegression  blkTs  more_rel_features       6    (10166, 2542)   
6  LinearRegression  blkTs  more_rel_features       7    (10166, 2542)   
7  LinearRegression  blkTs  more_rel_features       8    (10166, 2542)   
8  LinearRegression  blkTs  more_rel_features       9    (10166, 2542)   
9  LinearRegression  blkTs  more_rel_features      10    (10166, 2542)   

      Parameters          RMSE      MAPE           MAE      Variance  \
0  [5, 0.2, 0.4]     43.621182  0.072071     42.610168  2.098182e+03   
1  [5, 0.2, 0.4]    504.500436  0.162464    377.406845  1.824711e+05   
2  [5, 0.2, 0.4]   6194.267106  0.597242   5964.114674  4.482726e+07   
3  [5, 0.2, 0.4]    632.770316  0.060747    301.288880  1.481414e+06   
4  [5, 0.2, 0.4]   1820.430846  0.154890   1724.662909  3.062706e+06   
5  [5, 0.2, 0.4]    403.141027  0.044859    307.129100  1.472352e+06   
6  [5, 0.2, 0.4]   9807.260929  0.262562   8323.548362  7.282519e+07   
7  [5, 0.2, 0.4]   3465.073095  0.053601   2800.565306  2.017566e+07   
8  [5, 0.2, 0.4]  16086.657208  0.616827  13327.257491  3.608591e+08   
9  [5, 0.2, 0.4]   1408.008146  0.041944   1087.810930  3.311204e+06   

          R2  Adjusted_R2      Time  
0  -4.167710    -4.179941  0.697927  
1   0.058585     0.056357  0.784031  
2 -14.445556   -14.482114  1.611520  
3  -0.064618    -0.067138  0.725857  
4  -3.934844    -3.946524  0.881561  
5   0.825057     0.824643  0.751813  
6  -0.975546    -0.980222  0.775474  
7   0.589781     0.588810  0.625845  
8 -11.158163   -11.186940  0.715921  
9   0.649859     0.649030  1.522705

## Comparison table

In [37]:
# Define what model_info and evaluators in the Model Comparison Table
model_info = ['Model','Type', 'Features', 'Parameters']
evaluator_lst = ['RMSE','MAPE','MAE','Variance','R2','Adjusted_R2','Time']

# The the Cross Validation results would like to compare
comparison_lst = [simple_res_all, simple_res_more_rel, simple_res_less_rel, hyp_res, mul_cv_res, blk_cv_res]

In [38]:
# Show the Comparison Table
pd.concat([utilities.modelComparison(cv_result, model_info, evaluator_lst) for cv_result in comparison_lst])

Model        Type           Features       Parameters  \
0  LinearRegression      simple       all_features  [100, 0.0, 0.0]   
0  LinearRegression      simple  more_rel_features  [100, 0.0, 0.0]   
0  LinearRegression      simple  less_rel_features  [100, 0.0, 0.0]   
0  LinearRegression  autotuning  more_rel_features    [5, 0.2, 0.4]   
0  LinearRegression       mulTs  more_rel_features    [5, 0.2, 0.4]   
0  LinearRegression       blkTs  more_rel_features    [5, 0.2, 0.4]   

           RMSE      MAPE           MAE      Variance        R2  Adjusted_R2  \
0   4288.585097  0.124091   3461.845228  1.501965e+08  0.900484     0.900460   
0   9026.635554  0.219481   6967.905283  3.650631e+07  0.559123     0.559019   
0  14182.539053  0.314191  10899.108275  6.582993e+07 -0.088363    -0.088620   
0   1942.436008  0.068752   1465.138704  7.577615e+06  0.587808     0.587613   
0  11471.939678  0.410083  10101.898263  2.511092e+08 -1.797904    -1.798697   
0   4036.573029  0.206721   3425.639467  5.081995e+07 -3.262316    -3.272404   

       Time  
0  6.229855  
0  2.424016  
0  2.362139  
0  0.345756  
0  0.740428  
0  0.909265

## Training the final model

In [39]:
model = utilities.train_final_model(df, more_rel_features, params, MODEL_NAME, FEATURES_LABEL, TARGET_VAL)

In [40]:
GDRIVE_MODELS_DIR = GDRIVE_DIR + "/MyDrive/BDC/project/models"
GDRIVE_MODEL_NAME_EXT = GDRIVE_MODELS_DIR + "/" + MODEL_NAME

In [41]:
# Save the trained model
model.write().overwrite().save(GDRIVE_MODEL_NAME_EXT)